In [0]:
import pandas as pd
import json
from pyspark.sql import *
from pyspark.sql.functions import *

In [0]:

#Create mount point to access Data storage

dbutils.fs.mount(
  source = "wasbs://<container-name>@<storage-account-name>.blob.core.windows.net",
  mount_point = "/mnt/iotdata",
  extra_configs = {"fs.azure.account.key.<storage-account-name>.blob.core.windows.net":dbutils.secrets.get(scope = "<scope-name>", key = "<key-name>")})


Out[9]: True

In [0]:
dbutils.fs.ls('dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/')

Out[16]: [FileInfo(path='dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/CA_category_id.json', name='CA_category_id.json', size=7911, modificationTime=1662565847000),
 FileInfo(path='dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/DE_category_id.json', name='DE_category_id.json', size=7911, modificationTime=1662565847000),
 FileInfo(path='dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/FR_category_id.json', name='FR_category_id.json', size=7911, modificationTime=1662565847000),
 FileInfo(path='dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/GB_category_id.json', name='GB_category_id.json', size=8225, modificationTime=1662565847000),
 FileInfo(path='dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/IN_category_id.json', name='IN_category_id.json', size=8225, modificationTime=1662565847000),
 FileInfo(path='dbfs:/mnt/StorageDL/

In [0]:
#Get list of files available in folder
def get_json_files(directory_path):
    json_files = []
    files_to_treat = dbutils.fs.ls(directory_path)
    while files_to_treat:
        path = files_to_treat.pop(0).path
        if path.endswith('/'):
            files_to_treat += dbutils.fs.ls(path)
        elif path.endswith('.json'):
            json_files.append(path)
    return json_files

files = get_json_files('dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids')
print(files)

['dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/CA_category_id.json', 'dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/DE_category_id.json', 'dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/FR_category_id.json', 'dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/GB_category_id.json', 'dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/IN_category_id.json', 'dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/JP_category_id.json', 'dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/KR_category_id.json', 'dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/MX_category_id.json', 'dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/RU_category_id.json', 'dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysi

In [0]:
# Read all files and store in one DF

df = spark.read.option("multiline","true").json('dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Category_Ids/*.json')
df_items = df.select('items')
new_df = df_items.select(explode(col('items')).alias('normalized'))
proc_df = new_df.selectExpr('normalized.etag','normalized.id','normalized.kind','normalized.snippet.assignable','normalized.snippet.channelId','normalized.snippet.title')
display(proc_df)

etag id kind assignable channelId title "m2yskBQFythfE4irbTIeOgYYfBU/Xy1mB4_yLrHy_BmKmPBggty2mZQ" 1 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Film & Animation "m2yskBQFythfE4irbTIeOgYYfBU/UZ1oLIIz2dxIhO45ZTFR3a3NyTA" 2 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Autos & Vehicles "m2yskBQFythfE4irbTIeOgYYfBU/nqRIq97-xe5XRZTxbknKFVe5Lmg" 10 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Music "m2yskBQFythfE4irbTIeOgYYfBU/HwXKamM1Q20q9BN-oBJavSGkfDI" 15 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Pets & Animals "m2yskBQFythfE4irbTIeOgYYfBU/9GQMSRjrZdHeb1OEM1XVQ9zbGec" 17 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Sports "m2yskBQFythfE4irbTIeOgYYfBU/FJwVpGCVZ1yiJrqZbpqe68Sy_OE" 18 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Short Movies "m2yskBQFythfE4irbTIeOgYYfBU/M-3iD9dwK7YJCafRf_DkLN8CouA" 19 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Travel & Events "m2yskBQFythfE4irbTIeOgYYfBU/WmA0qYEfjWsAoyJFSw2zinhn2wM" 20 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Gaming "m2yskBQFythfE4irbTIeOgYYfBU/EapFaGYG7K0StIXVf8aba249tdM" 21 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Videoblogging "m2yskBQFythfE4irbTIeOgYYfBU/xId8RX7vRN8rqkbYZbNIytUQDRo" 22 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ People & Blogs "m2yskBQFythfE4irbTIeOgYYfBU/G9LHzQmx44rX2S5yaga_Aqtwz8M" 23 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Comedy "m2yskBQFythfE4irbTIeOgYYfBU/UVB9oxX2Bvqa_w_y3vXSLVK5E_s" 24 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Entertainment "m2yskBQFythfE4irbTIeOgYYfBU/QiLK0ZIrFoORdk_g2l_XR_ECjDc" 25 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ News & Politics "m2yskBQFythfE4irbTIeOgYYfBU/r6Ck6Z0_L0rG37VJQR200SGNA_w" 26 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Howto & Style "m2yskBQFythfE4irbTIeOgYYfBU/EoYkczo9I3RCf96RveKTOgOPkUM" 27 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Education "m2yskBQFythfE4irbTIeOgYYfBU/w5HjcTD82G_XA3xBctS30zS-JpQ" 28 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Science & Technology "m2yskBQFythfE4irbTIeOgYYfBU/SalkJoBWq_smSEqiAx_qyri6Wa8" 29 youtube#videoCategory true UCBR8-60-B28hp2BmDPdntcQ Nonprofits & Activism "m2yskBQFythfE4irbTIeOgYYfBU/lL7uWDr_071CHxifjYG1tJrp4Uo" 30 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Movies "m2yskBQFythfE4irbTIeOgYYfBU/WnuVfjO-PyFLO7NTRQIbrGE62nk" 31 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Anime/Animation "m2yskBQFythfE4irbTIeOgYYfBU/ctpH2hGA_UZ3volJT_FTlOg9M00" 32 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Action/Adventure "m2yskBQFythfE4irbTIeOgYYfBU/L0kR3-g1BAo5UD1PLVbQ7LkkDtQ" 33 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Classics "m2yskBQFythfE4irbTIeOgYYfBU/pUZOAC_s9sfiwar639qr_wAB-aI" 34 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Comedy "m2yskBQFythfE4irbTIeOgYYfBU/Xb5JLhtyNRN3AQq021Ds-OV50Jk" 35 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Documentary "m2yskBQFythfE4irbTIeOgYYfBU/u8WXzF4HIhtEi805__sqjuA4lEk" 36 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Drama "m2yskBQFythfE4irbTIeOgYYfBU/D04PP4Gr7wc4IV_O9G66Z4A8KWQ" 37 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Family "m2yskBQFythfE4irbTIeOgYYfBU/i5-_AceGXQCEEMWU0V8CcQm_vLQ" 38 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Foreign "m2yskBQFythfE4irbTIeOgYYfBU/rtlxd0zOixA9QHdIZB26-St5qgQ" 39 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Horror "m2yskBQFythfE4irbTIeOgYYfBU/N1TrDFLRppxZgBowCJfJCvh0Dpg" 40 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Sci-Fi/Fantasy "m2yskBQFythfE4irbTIeOgYYfBU/7UMGi6zRySqXopr_rv4sZq6Za2E" 41 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Thriller "m2yskBQFythfE4irbTIeOgYYfBU/RScXhi324h8usyIetreAVb-uKeM" 42 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Shorts "m2yskBQFythfE4irbTIeOgYYfBU/0n9MJVCDLpA8q7aiGVrFsuFsd0A" 43 youtube#videoCategory false UCBR8-60-B28hp2BmDPdntcQ Shows "m2yskBQFythfE4irbTIeOgYYfBU/x5NxSf5fz8hn4loSN4rvhwzD_pY" 44 youtube#videoCateg

In [0]:
#Writing Cleaned json file to cleaned folder in Storage account
proc_df.write \
    .format("parquet") \
    .mode("Overwrite") \
    .option("path","dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_cleaned/json_data/") \
    .save()

In [0]:
##############################################################################################################
#Reading csv data and storing it in csv
##############################################################################################################

In [0]:
#setting custom schema
sche = '''
    video_id string,
 trending_date string,
 title string,
 channel_title string,
 category_id double,
 publish_time string,
 tags string,
 views double,
 likes double,
 dislikes double,
 comment_count double,
 thumbnail_link string,
 comments_disabled boolean,
 ratings_disabled boolean,
 video_error_or_removed boolean,
 description string
'''

df_csv = spark.read.format("csv") \
        .option("header","true") \
        .schema(sche) \
        .load("dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_raw/Video_Data/*.csv")
display(df_csv)


video_id trending_date title channel_title category_id publish_time tags views likes dislikes comment_count thumbnail_link comments_disabled ratings_disabled video_error_or_removed description gDuslQ9avLc 17.14.11 Захар и Полина учатся экономить Т—Ж БОГАЧ 22.0 2017-11-13T09:09:31.000Z "захар и полина|""учимся экономить""|""копить деньги""|""экономь""|""мелкие траты""|""как экономить на еде""|""советы экономить""|""личный бюджет""|""при маленькой зарплате""|""свадьба""|""подготовка к свадьбе""|""гости на свадьбе""|""красивая свадьба""|""жизнь свадьба""" 62408.0 334.0 190.0 50.0 https://i.ytimg.com/vi/gDuslQ9avLc/default.jpg false false false Знакомьтесь, это Захар и Полина. Вместе с ними мы сняли серию роликов о семейном бюджете, экономии и тратах. В первом ролике ребята готовятся к свадьбе и хотят отпраздновать ее пышно. Но без накоплений, с одной зарплатой на двоих и кучей мелких трат свадьба может не случиться. Смотрите, как спасти семейный бюджет и научиться копить. В следующем ролике расскажем, как заработать больше, если денег все равно не хватает.\n\nТаблица для ежедневного бюджета: https://journal.tinkoff.ru/spreadsheet/\n\nПодписывайтесь на наш канал и узнавайте, как с умом пользоваться деньгами: https://www.youtube.com/tinkoffjournal\n\nГотовы рассказать свою историю или стать автором канала — пишите на rich@tinkoff.ru AOCJIFEA_jE 17.14.11 Биржа Мемов #29. Большой выпуск Druzhko Show 22.0 2017-11-13T17:32:11.000Z "биржа мемов|""лев шагинян""|""мемы""|""пикчи""|""дружко""|""дружко шоу""|""анонимус""|""борщ""|""ftp""|""мхк""|""на случай важных переговоров""|""аффлек""|""бэн аффлек""|""batman""|""бэтмен""|""трамп""" 330043.0 43841.0 2244.0 2977.0 https://i.ytimg.com/vi/AOCJIFEA_jE/default.jpg false false false В 29 выпуске Дружко Шоу Сергей сказал, что Биржа Мемов отдельно выйдет на его канале в понедельник…и не соврал!\n\nВстречайте, расширенная и, впервые, самостоятельная Биржа Мемов, в которой Лев вспомнил лучшие пикчи последней недели, обсудил самые мемные новости, встретился с очередным гостем и разобрал один из пабликов ВК на орпригодность в рамках своей новой рубрики! В общем, обязательно к просмотру.\n\nВедущий биржи мемов: \nVK: https://vk.cc/6Dolqn\nInstagram: https://goo.gl/AoHGPN\n\nБиржа Мемов:\nhttps://vk.com/stockmem\n\nГруппа Вконтакте: https://vk.cc/6BBS07\nГруппа Facebook: https://goo.gl/ZS5mzT\nInstagram Шоу: https://goo.gl/F5s5PK\n\nМоя личная страница ВКонтакте: https://vk.cc/6Djxew\nМой инстаграм: https://goo.gl/LukuVV\n\nИван #ЖаданИсполняетМечты:\nVK: https://vk.cc/70ncIe\nInstagram: https://goo.gl/DVjC87 VAWNQDgwwOM 17.14.11 ХАЙП КЭМП - СВОЙ СРЕДИ ЧУЖИХ Юлик 24.0 2017-11-13T16:11:31.000Z "юмор|""комедия""|""влог""|""блог""|""смешно""|""смешное""|""juliusspeak""|""julius speak""|""джулиус спик""|""юлик""|""шутки""|""приколы""|""видеоприколы""|""хайп кэмп""" 424596.0 49854.0 714.0 2944.0 https://i.ytimg.com/vi/VAWNQDgwwOM/default.jpg false false false http://kapitany.ru/!Yulik.cap - Факультет #Капитаны\nМерч - https://mamcupy.com/shop/pap-prodaj/yulik\nЮлик - http://vk.com/oneshko\nГруппа - http://vk.com/juliusspeak\nЛайв канал - https://www.youtube.com/channel/UCvnVq3ay_VTc6NuwwfUzVJQ?sub_confirmation=1 gknkFwKQfHg 17.14.11 Сочная кесадилья с курицей Hochland 22.0 2017-11-13T06:51:10.000Z "хохланд|""сыр""|""рецепты""|""как приготовить""|""вкусно""|""быстро""" 112851.0 3566.0 122.0 80.0 https://i.ytimg.com/vi/gknkFwKQfHg/default.jpg false false false *** как готовить ресторанные блюда дома 3sYvZcwzZr8 17.14.11 КЛИПЫ РОДИТЕЛЕЙ НА ШКОЛЬНЫЙ ВЫПУСКНОЙ Совергон 24.0 2017-11-13T16:52:36.000Z "Совергон|""Sovergon""|""клипы""|""родители""|""школа""|""школьники""|""школьница""|""выпускной""|""последний звонок""|""звонок""|""музыка""|""юмор""|""скетч""|""шоу""|""совергон +""|""мама""|""папа""|""класс""|""11А""|""9А""|""учителя""|""1 сентября""|""обзор""|""тренды""|""реакция""|""мемы""|""видео""|""обзор трендов""|""в тренде""|""горячее""|""засмеялся проиграл""|""тает лёд""|""пародия""" 243469.0 36216.0 631.0

In [0]:
#creating Region column for partition to save file in parquet
test = df_csv.withColumn("file_name",input_file_name())
final_df = test.withColumn("region",substring('file_name',-12,2)).drop('file_name')
display(final_df)


video_id trending_date title channel_title category_id publish_time tags views likes dislikes comment_count thumbnail_link comments_disabled ratings_disabled video_error_or_removed description region gDuslQ9avLc 17.14.11 Захар и Полина учатся экономить Т—Ж БОГАЧ 22.0 2017-11-13T09:09:31.000Z "захар и полина|""учимся экономить""|""копить деньги""|""экономь""|""мелкие траты""|""как экономить на еде""|""советы экономить""|""личный бюджет""|""при маленькой зарплате""|""свадьба""|""подготовка к свадьбе""|""гости на свадьбе""|""красивая свадьба""|""жизнь свадьба""" 62408.0 334.0 190.0 50.0 https://i.ytimg.com/vi/gDuslQ9avLc/default.jpg false false false Знакомьтесь, это Захар и Полина. Вместе с ними мы сняли серию роликов о семейном бюджете, экономии и тратах. В первом ролике ребята готовятся к свадьбе и хотят отпраздновать ее пышно. Но без накоплений, с одной зарплатой на двоих и кучей мелких трат свадьба может не случиться. Смотрите, как спасти семейный бюджет и научиться копить. В следующем ролике расскажем, как заработать больше, если денег все равно не хватает.\n\nТаблица для ежедневного бюджета: https://journal.tinkoff.ru/spreadsheet/\n\nПодписывайтесь на наш канал и узнавайте, как с умом пользоваться деньгами: https://www.youtube.com/tinkoffjournal\n\nГотовы рассказать свою историю или стать автором канала — пишите на rich@tinkoff.ru RU AOCJIFEA_jE 17.14.11 Биржа Мемов #29. Большой выпуск Druzhko Show 22.0 2017-11-13T17:32:11.000Z "биржа мемов|""лев шагинян""|""мемы""|""пикчи""|""дружко""|""дружко шоу""|""анонимус""|""борщ""|""ftp""|""мхк""|""на случай важных переговоров""|""аффлек""|""бэн аффлек""|""batman""|""бэтмен""|""трамп""" 330043.0 43841.0 2244.0 2977.0 https://i.ytimg.com/vi/AOCJIFEA_jE/default.jpg false false false В 29 выпуске Дружко Шоу Сергей сказал, что Биржа Мемов отдельно выйдет на его канале в понедельник…и не соврал!\n\nВстречайте, расширенная и, впервые, самостоятельная Биржа Мемов, в которой Лев вспомнил лучшие пикчи последней недели, обсудил самые мемные новости, встретился с очередным гостем и разобрал один из пабликов ВК на орпригодность в рамках своей новой рубрики! В общем, обязательно к просмотру.\n\nВедущий биржи мемов: \nVK: https://vk.cc/6Dolqn\nInstagram: https://goo.gl/AoHGPN\n\nБиржа Мемов:\nhttps://vk.com/stockmem\n\nГруппа Вконтакте: https://vk.cc/6BBS07\nГруппа Facebook: https://goo.gl/ZS5mzT\nInstagram Шоу: https://goo.gl/F5s5PK\n\nМоя личная страница ВКонтакте: https://vk.cc/6Djxew\nМой инстаграм: https://goo.gl/LukuVV\n\nИван #ЖаданИсполняетМечты:\nVK: https://vk.cc/70ncIe\nInstagram: https://goo.gl/DVjC87 RU VAWNQDgwwOM 17.14.11 ХАЙП КЭМП - СВОЙ СРЕДИ ЧУЖИХ Юлик 24.0 2017-11-13T16:11:31.000Z "юмор|""комедия""|""влог""|""блог""|""смешно""|""смешное""|""juliusspeak""|""julius speak""|""джулиус спик""|""юлик""|""шутки""|""приколы""|""видеоприколы""|""хайп кэмп""" 424596.0 49854.0 714.0 2944.0 https://i.ytimg.com/vi/VAWNQDgwwOM/default.jpg false false false http://kapitany.ru/!Yulik.cap - Факультет #Капитаны\nМерч - https://mamcupy.com/shop/pap-prodaj/yulik\nЮлик - http://vk.com/oneshko\nГруппа - http://vk.com/juliusspeak\nЛайв канал - https://www.youtube.com/channel/UCvnVq3ay_VTc6NuwwfUzVJQ?sub_confirmation=1 RU gknkFwKQfHg 17.14.11 Сочная кесадилья с курицей Hochland 22.0 2017-11-13T06:51:10.000Z "хохланд|""сыр""|""рецепты""|""как приготовить""|""вкусно""|""быстро""" 112851.0 3566.0 122.0 80.0 https://i.ytimg.com/vi/gknkFwKQfHg/default.jpg false false false *** как готовить ресторанные блюда дома RU 3sYvZcwzZr8 17.14.11 КЛИПЫ РОДИТЕЛЕЙ НА ШКОЛЬНЫЙ ВЫПУСКНОЙ Совергон 24.0 2017-11-13T16:52:36.000Z "Совергон|""Sovergon""|""клипы""|""родители""|""школа""|""школьники""|""школьница""|""выпускной""|""последний звонок""|""звонок""|""музыка""|""юмор""|""скетч""|""шоу""|""совергон +""|""мама""|""папа""|""класс""|""11А""|""9А""|""учителя""|""1 сентября""|""обзор""|""тренды""|""реакция""|""мемы""|""видео""|""обзор трендов""|""в тренде""|""горячее""|""засмеялся проиграл""|""тает лёд""|""пародия""" 243

In [0]:
#writing results back to storage account in parquet format
final_df.write \
    .format("parquet") \
    .partitionBy("region") \
    .mode("Overwrite") \
    .option("path","dbfs:/mnt/StorageDL/YouTube_data_analysis/Youtube_Data_Analysis_cleaned/csv_data/") \
    .save()
